In [1]:
import hexathello.aiPlayers as aiPlayers
import hexathello.autoPlayer as autoPlayer
import hexathello.engine as engine
import hexathello.history as history
import hexathello.jable as jable
import hexathello.printing as printing

import numpy as np

from os import path

# -- Settings
game_size: int = 5
player_count: int = 2

In [2]:
history_dir: str = path.join(
    'data',
    'history',
    'examples'
)
assert path.isdir(
    history_dir
)

baseline_data_path: str = path.join(
    history_dir,
    'greendom_size-{}_players-{}.json'.format(
        game_size, player_count
    )
)
   

In [3]:
# Read the data from disk to learn from
print("# Reading history from {}".format( baseline_data_path ) )
history_fromDisk: jable.JyFrame = jable.read_file(
    baseline_data_path
)

# Decode the state, option, and play vectors from integers to numpy arrays
history_decoded: jable.JyFrame = history.history_fromInt(
    history_fromDisk
)

assert len( history_decoded ) >= 20000
    
# Make it PoV 0 to appropriately learn
povHistory: jable.JyFrame = history.povHistory_from_literalHistory(
    history_decoded
)

del history_decoded
del history_fromDisk

# Reading history from data/history/examples/greendom_size-5_players-2.json


In [4]:
# We want to train a Keras Neural Network on the data we have.
# The input size is the length of a state vector
# The output size is the length of the play vector
# Take both from the first row
input_size: int = len( povHistory[0,'board_state'] )
output_size: int = len( povHistory[0, 'player_action'] )

# The `KerasHexAgent` subclass of `HexAgent` has a `brain` property; this is the neural network
# We could in fact us any objects conforming to the `PredictionModel` protocol, which has methods:
#   - fit()
#   - predict()
#   - call()
#
# We're going to train it on the Greendom data
# Match the input to a board state vector
import tensorflow as tf

def init_brain(
    inner_layer_size: int,
    layers: int,
    activation: str,
    learning_rate: float = 0.005
    ) -> tf.keras.Model:
    brain_input = tf.keras.layers.Input(
        shape = (input_size,),
        name = 'keras_tensor'
    )
    
    assert layers > 0
    brain_next = tf.keras.layers.Dense(
        inner_layer_size,
        activation = activation
    )( brain_input )
    
    if layers > 1:
        for _ in range( 1, layers ):
            brain_next = tf.keras.layers.Dense(
                inner_layer_size,
                activation = activation
            )( brain_next )
        #
    #/if layers > 1
    brain_output = tf.keras.layers.Dense(
        output_size,
        activation = 'sigmoid'
    )( brain_next )
    
    brain_model: tf.keras.Model = tf.keras.Model(
        brain_input,
        brain_output
    )
        
    brain_model.compile(
        optimizer = tf.keras.optimizers.Adam(
            learning_rate = 0.005
        ),
        loss = tf.keras.losses.CategoricalCrossentropy()
    )
    
    return brain_model
#/def init_brain
    
# Initial AI Agents
brain_0: tf.keras.Model = init_brain(
    inner_layer_size = 200,
    layers = 5,
    activation = 'relu'
)
ai_keras_0: aiPlayers.KerasHexAgent = aiPlayers.KerasHexAgent(
    size = game_size,
    player_count = player_count,
    brain = brain_0,
    player_id = None,
    ai_id = 'custom_200-5',
    p_random = 0.3
)
ai_keras_0.train(
    game_history = povHistory,
    epochs = 50
)

brain_1: tf.keras.Model = init_brain(
    inner_layer_size = 100,
    layers = 10,
    activation = 'relu'
)
ai_keras_1: aiPlayers.KerasHexAgent = aiPlayers.KerasHexAgent(
    size = game_size,
    player_count = player_count,
    brain = brain_1,
    player_id = None,
    ai_id = 'custom_100-10',
    p_random = 0.3
)
ai_keras_1.train(
    game_history = povHistory,
    epochs = 50
)


if False:
    # Set the checkpoint to save
    ai_keras_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
        filepath=ai_keras_path,
        monitor='loss',
        mode='min',
        save_best_only=True
    )

    ai_keras_0.train(
        game_history = povHistory,
        epochs = 10,
        callbacks = [ ai_keras_checkpoint_callback ]
    )
#

2025-05-07 19:21:25.524933: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


Epoch 1/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 2s 1ms/step - loss: 1.6387
Epoch 2/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4263
Epoch 3/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3463
Epoch 4/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.2996
Epoch 5/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.2695
Epoch 6/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.2342
Epoch 7/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.1809
Epoch 8/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.1659
Epoch 9/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.1190
Epoch 10/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.1011
Epoch 11/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.0904
Epoch 12/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.0709
Epoch 13/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.0267
Epoch 14/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.0155
Epoch 15/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - lo

626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4647
Epoch 32/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4466
Epoch 33/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4585
Epoch 34/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4252
Epoch 35/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4373
Epoch 36/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4315
Epoch 37/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4261
Epoch 38/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4769
Epoch 39/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4059
Epoch 40/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3981
Epoch 41/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4672
Epoch 42/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4398
Epoch 43/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.5023
Epoch 44/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.5046
Epoch 45/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss:

In [8]:
# Have them play eachother to start it off
keras_history_0: jable.JyFrame = autoPlayer.runHexathello_withAgents(
    agents = [ai_keras_0, ai_keras_1],
    size = game_size,
    logging_level = 0
)
keras_history_0.makeColumn_shift( "winner" )
keras_history_0.makeColumn_shift( "scores" )    
print( keras_history_0 )

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 19 - 22; Player 1 wins
# Game done
{'winner': 

In [9]:
# Get many games played
while len( keras_history_0 ) <= 20000:
    next_history: jable.JyFrame = autoPlayer.runHexathello_withAgents(
        agents = [ai_keras_0, ai_keras_1],
        size = game_size,
        logging_level = 0
    )
        
    
    keras_history_0.extend( next_history )
#

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, n

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 20 - 22; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [20, 22]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Early end, no move for any player
RESULT: 27 - 15; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [27, 15]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 16 - 26; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [16, 26]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Early end, no move for any player
RESULT: 24 - 18; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [24, 18]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 29 - 13; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [29, 13]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Early end, no move for any player
RESULT: 16 - 26; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [16, 26]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Early end, no move for any player
RESULT: 15 - 27; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [15, 27]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
Early end, no move for any player
RESULT: 14 - 28; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [14, 28]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 38 - 4; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [38, 4]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━

In [10]:
# Run the loop of training and improving
def run_training_loop(
    history: jable.JyFrame,
    data_points: int,
    inner_layer_size: list[ int ],
    layers: list[ int ],
    activation: list[ str ],
    p_random: float = 0.2,
    epochs: int = 50,
    learning_rate: float = 0.005
    ) -> jable.JyFrame:

    brain_0: tf.keras.Model = init_brain(
        inner_layer_size = inner_layer_size[0],
        layers = layers[0],
        activation = activation[0],
        learning_rate = learning_rate
    )
    ai_keras_0: aiPlayers.KerasHexAgent = aiPlayers.KerasHexAgent(
        size = game_size,
        player_count = player_count,
        brain = brain_0,
        player_id = None,
        ai_id = 'custom_{}-{}'.format( inner_layer_size[0], layers[0] ),
        p_random = p_random
    )
    ai_keras_0.train(
        game_history = history,
        epochs = epochs,
    )

    brain_1: tf.keras.Model = init_brain(
        inner_layer_size = inner_layer_size[1],
        layers = layers[1],
        activation = activation[1],
        learning_rate = learning_rate
    )
    ai_keras_1: aiPlayers.KerasHexAgent = aiPlayers.KerasHexAgent(
        size = game_size,
        player_count = player_count,
        brain = brain_1,
        player_id = None,
        ai_id = 'custom_{}-{}'.format( inner_layer_size[1], layers[1] ),
        p_random = p_random
    )
    ai_keras_1.train(
        game_history = history,
        epochs = epochs
    )

    # Have them play eachother now that they're trained
    history = autoPlayer.runHexathello_withAgents(
        agents = [ai_keras_0, ai_keras_1],
        size = game_size,
        logging_level = 0
    )
    history.makeColumn_shift( "winner" )
    history.makeColumn_shift( "scores" )

    while len( history ) < data_points:
        next_history: jable.JyFrame = autoPlayer.runHexathello_withAgents(
            agents = [ai_keras_0, ai_keras_1],
            size = game_size,
            logging_level = 0
        )

        history.extend( next_history )
        print("# {}/{} moves".format( len(history), data_points ))
    #    #
    return history
#

for i in range( 5 ):
    fp: str = path.join(
        history_dir,
        'bigger_history_{}.json'.format( i )
    )
    if path.isfile( fp ):
        keras_history_0 = history.history_fromInt(
            jable.from_file(
                fp
            )
        )
    #
    else:
        keras_history_0: jable.JyFrame = run_training_loop(
            history = keras_history_0,
            data_points = 20000,
            inner_layer_size = [200, 100],
            layers = [5, 10],
            activation = ['relu', 'relu'],
            p_random = 0.3,
            epochs = 50
        )
        history.history_asInt(
            keras_history_0
        ).write_file(
            fp
        )
    #/if path.isfile( fp )/else
#/for i in range( 5 )



Starting training loop 0
Epoch 1/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 2s 1ms/step - loss: 1.6739
Epoch 2/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.5489
Epoch 3/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.5121
Epoch 4/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4789
Epoch 5/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4554
Epoch 6/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4329
Epoch 7/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3993
Epoch 8/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3631
Epoch 9/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3422
Epoch 10/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3252
Epoch 11/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.3036
Epoch 12/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.2991
Epoch 13/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.2710
Epoch 14/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.2790
Epoch 15/50
626/626 ━━━━━━━━━━━━

626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - loss: 1.4318
Epoch 32/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4595
Epoch 33/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4198
Epoch 34/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.8177
Epoch 35/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4218
Epoch 36/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.7085
Epoch 37/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.6201
Epoch 38/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4825
Epoch 39/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.3832
Epoch 40/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 14.1472
Epoch 41/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4689
Epoch 42/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4345
Epoch 43/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 1.4520
Epoch 44/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 3.4001
Epoch 45/50
626/626 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
Early end, no move for any player
RESULT: 6 - 35; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 35, 'size': 5, 'game_complete': True, 'empty_count': 20, 'player_count': 2, 'current_player': 1, 'scores': [6, 35]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
Early end, no move for any player
RESULT: 26 - 16; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [26, 16]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
Early end, no move for any player
RESULT: 13 - 29; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [13, 29]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 19 - 23; Player 1 wins
# Game done
{'winner': 1, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [19, 23]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Early end, no move for any player
RESULT: 22 - 20; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [22, 20]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
Early end, no move for any player
RESULT: 22 - 20; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 0, 'scores': [22, 20]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Early end, no move for any player
RESULT: 29 - 13; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [29, 13]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Early end, no move for any player
RESULT: 24 - 18; Player 0 wins
# Game done
{'winner': 0, 'turn_index': 36, 'size': 5, 'game_complete': True, 'empty_count': 19, 'player_count': 2, 'current_player': 1, 'scores': [24, 18]}
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━

In [ ]:
# Make a final much bigger data set with 100k data points
history_big_0: jable.JyFrame = keras_history_0 = run_training_loop(
    history = keras_history_0,
    data_points = 100000,
    inner_layer_size = [200, 100],
    layers = [5, 10],
    activation = ['relu', 'relu'],
    p_random = 0.3,
    epochs = 50
)
    
history.history_asInt(
    history_big_0
).write_file(
    fp = path.join(
        history_dir,
        'biggest_history_0.json'
    )
)

In [ ]:
print("# Done")